<script>
  jQuery(document).ready(function($) {

  $(window).load(function(){
    $('#preloader').fadeOut('slow',function(){$(this).remove();});
  });

  });
</script>

<style type="text/css">
  div#preloader { position: fixed;
      left: 0;
      top: 0;
      z-index: 999;
      width: 100%;
      height: 100%;
      overflow: visible;
      background: #fff url('http://preloaders.net/preloaders/720/Moving%20line.gif') no-repeat center center;
  }

</style>

<div id="preloader"></div>

<script>
  function code_toggle() {
    if (code_shown){
      $('div.input').hide('500');
      $('#toggleButton').val('Show Code')
    } else {
      $('div.input').show('500');
      $('#toggleButton').val('Hide Code')
    }
    code_shown = !code_shown
  }

  $( document ).ready(function(){
    code_shown=false;
    $('div.input').hide()
  });
</script>
<form action="javascript:code_toggle()"><input type="submit" id="toggleButton" value="Show Code"></form>

In [445]:
from sklearn.feature_extraction.text import TfidfVectorizer
from gensim.summarization import summarize, keywords
from nltk.stem.wordnet import WordNetLemmatizer
from gensim.models.word2vec import Word2Vec
from nltk.stem.porter import PorterStemmer
from nltk.corpus import stopwords
from sklearn.manifold import TSNE
from collections import Counter
from wordcloud import WordCloud
import matplotlib.pyplot as mp
from string import punctuation
import seaborn as sns
import pandas as pd
import numpy as np
import itertools
import random
import string
import nltk
import re

import matplotlib.pyplot as mp
%matplotlib inline

from plotly.offline import download_plotlyjs
from plotly.offline import init_notebook_mode
from plotly.offline import plot, iplot
import cufflinks as cf
cf.go_offline()

stoplist = stopwords.words('english')

# Read data from csv file
data = pd.read_csv('/Users/degravek/Downloads/Tweets.csv', header=0)

data = data[data['airline_sentiment'] != 'neutral']
data = data.drop_duplicates('text').reset_index(drop=True)

In [446]:
data.head()

tweet_id airline_sentiment  airline_sentiment_confidence  \
0  570301130888122368          positive                        0.3486   
1  570301031407624196          negative                        1.0000   
2  570300817074462722          negative                        1.0000   
3  570300767074181121          negative                        1.0000   
4  570300616901320704          positive                        0.6745   

  negativereason  negativereason_confidence         airline  \
0            NaN                     0.0000  Virgin America   
1     Bad Flight                     0.7033  Virgin America   
2     Can't Tell                     1.0000  Virgin America   
3     Can't Tell                     0.6842  Virgin America   
4            NaN                     0.0000  Virgin America   

  airline_sentiment_gold        name negativereason_gold  retweet_count  \
0                    NaN    jnardino                 NaN              0   
1                    NaN    jnardino                 NaN              0   
2                    NaN    jnardino                 NaN              0   
3                    NaN    jnardino                 NaN              0   
4                    NaN  cjmcginnis                 NaN              0   

                                                text tweet_coord  \
0  @VirginAmerica plus you've added commercials t...         NaN   
1  @VirginAmerica it's really aggressive to blast...         NaN   
2  @VirginAmerica and it's a really big bad thing...         NaN   
3  @VirginAmerica seriously would pay $30 a fligh...         NaN   
4  @VirginAmerica yes, nearly every time I fly VX...         NaN   

               tweet_created    tweet_location               user_timezone  
0  2015-02-24 11:15:59 -0800               NaN  Pacific Time (US & Canada)  
1  2015-02-24 11:15:36 -0800               NaN  Pacific Time (US & Canada)  
2  2015-02-24 11:14:45 -0800               NaN  Pacific Time (US & Canada)  
3  2015-02-24 11:14:33 -0800               NaN  Pacific Time (US & Canada)  
4  2015-02-24 11:13:57 -0800  San Francisco CA  Pacific Time (US & Canada)

In [936]:
plot = data['airline_sentiment'].value_counts().iplot(kind="bar", xTitle='Sentiment', color='#5A77A5',
                            yTitle='Counts', dimensions=(780,400), margin=(100,100,40,0))

In [953]:
punctuation = '!"#?$%“”&\'()’—*+,-./:;<=>@[\\]^_`{|}~'
def process_text(text):
    result = re.sub(r'(@\S+)', '', text).lower()                         # lowercase
    result = result.replace('\n', ' ').replace('\\n', ' ')               # remove new
    result = re.sub(r'[\?\.\!]+', '. ', result)                          # multiple
    result = re.sub('((www\S+)|(http\S+))', '', result)                  # remove links
    result = re.sub(r'[-+]?\d*[.,]\d+|\d+', 'number', result)            # numbers
    result = ''.join(word for word in result if word not in punctuation) # punctuation
    result = re.sub(r'(\w)(\1{2,})', r'\1', result)                      # white space
    return result

def rmstopwords(text):
    result = text.lower().split()
    result = ' '.join(word for word in result
                      if word not in stoplist)
    return result

def sent_boundaries(text):
    result = re.sub(r'(@\S+)', '', text)
    result = re.sub(r'(.RT\S+)', '', result)
    result = re.sub(r'[\?\.\!]+', '. ', result)
    return result

def tokenize_sent(text):
    result = nltk.sent_tokenize(text)
    result = [sent for sent in result]
    return ''.join(result)

def ngrams(text, n):
    result = []
    text = text.split()
    if n==1:
        partspeech = nltk.pos_tag(text)
        result = [word for word, pos in
                  partspeech if pos[0] == 'N']
    else:
        for i in range(len(text)-(n-1)):
            result.append('_'.join(text[i:i+n]))
    return result

def num_words(text):
    s = text.split()
    num = len([word for word in s if word])
    return num

def num_exc_ques(text):
    result = len(re.findall('[.!?]', text))
    return result

Let's see what's being talked about.

# n-Gram Analysis

In [509]:
data['pro_text'] = data['text'].apply(process_text)

data['ngram_1']   = data['pro_text'].apply(rmstopwords).apply(ngrams, args=(1,))
data['ngram_2']   = data['pro_text'].apply(rmstopwords).apply(ngrams, args=(2,))
data['ngram_3']   = data['pro_text'].apply(rmstopwords).apply(ngrams, args=(3,))

data[['text','ngram_1','ngram_2','ngram_3']].head()

text  \
0  @VirginAmerica plus you've added commercials t...   
1  @VirginAmerica it's really aggressive to blast...   
2  @VirginAmerica and it's a really big bad thing...   
3  @VirginAmerica seriously would pay $30 a fligh...   
4  @VirginAmerica yes, nearly every time I fly VX...   

                                    ngram_1  \
0   [youve, commercials, experience, tacky]   
1  [blast, entertainment, guests, recourse]   
2                                   [thing]   
3        [number, flight, seats, thing, va]   
4                        [time, worm, wont]   

                                             ngram_2  \
0  [plus_youve, youve_added, added_commercials, c...   
1  [really_aggressive, aggressive_blast, blast_ob...   
2                   [really_big, big_bad, bad_thing]   
3  [seriously_would, would_pay, pay_number, numbe...   
4  [yes_nearly, nearly_every, every_time, time_fl...   

                                             ngram_3  
0  [plus_youve_added, youve_added_commercials, ad...  
1  [really_aggressive_blast, aggressive_blast_obn...  
2                    [really_big_bad, big_bad_thing]  
3  [seriously_would_pay, would_pay_number, pay_nu...  
4  [yes_nearly_every, nearly_every_time, every_ti...

Check out the most common n-grams in the two classes

In [560]:
def frequent_tokens(category, n, num):
    if n == 'chunk':
        tokens = data[data['airline_sentiment'] == category]['chunk']
    else:
        tokens = data[data['airline_sentiment'] == category]['ngram_' + str(n)]
    alltokens = []
    for token_list in tokens:
        alltokens += token_list
    counter = Counter(alltokens)
    return counter.most_common(num)

In [562]:
for category in set(data['airline_sentiment']):
    print(category, "sentiment")
    print("1-grams:", frequent_tokens(category, 1, 10))
    print('--------------------')
    print("2-grams:", frequent_tokens(category, 2, 10))
    print('--------------------')
    print("3-grams:", frequent_tokens(category, 3, 10))
    print('--------------------')

positive sentiment
1-grams: [('thanks', 578), ('flight', 372), ('thank', 349), ('number', 343), ('service', 157), ('customer', 112), ('guys', 98), ('time', 95), ('today', 82), ('airline', 78)]
--------------------
2-grams: [('customer_service', 91), ('flight_number', 68), ('thank_much', 36), ('thanks_much', 28), ('great_flight', 27), ('thanks_help', 22), ('great_job', 22), ('cant_wait', 21), ('flight_attendant', 20), ('looking_forward', 18)]
--------------------
3-grams: [('great_customer_service', 14), ('keep_good_work', 12), ('crew_flight_number', 9), ('excellent_customer_service', 7), ('amazing_customer_service', 7), ('reflight_booking_problems', 7), ('customer_service_today', 6), ('flight_number_bos', 5), ('flight_booking_problems', 5), ('love_flying_guys', 5)]
--------------------
negative sentiment
1-grams: [('number', 4078), ('flight', 2879), ('service', 734), ('hours', 642), ('customer', 600), ('time', 582), ('help', 498), ('plane', 455), ('hour', 439), ('flights', 414)]
------

Explain common ngrams. Let's plot the top 15 3-grams for the negative class.

In [572]:
ngram = pd.DataFrame(frequent_tokens('negative', 3, 10), columns=['ngram_3','counts'])

In [574]:
plot = ngram.iplot(kind="bar", x='ngram_3', y='counts', xTitle='3-gram', color='#5A77A5',
                            yTitle='Counts', dimensions=(780,500), margin=(100,100,120,0))

Let's try chunking.

In [524]:
def extract_candidate_chunks(text, grammar = 'CHUNK: {<JJ.*>*<NN.*>+}'):
    import itertools, nltk, string
    parser = nltk.RegexpParser(grammar)
    tagged_sents = [nltk.pos_tag(nltk.word_tokenize(text))]

    for chunk in tagged_sents:
        if not chunk:
            candidates = []
        else:
            candidates = []
            tree = parser.parse(chunk)
            for subtree in tree.subtrees():
                if subtree.label() == 'CHUNK':
                    candidates.append(('_'.join([word for (word, tag) in subtree.leaves()])))
    candidates = [word for word in candidates if word not in stoplist]
    return candidates

In [520]:
data['chunk'] = data['pro_text'].apply(extract_candidate_chunks)

In [530]:
for category in set(data['airline_sentiment']):
    print(category, "sentiment")
    print("chunk:", frequent_tokens(category, "chunk"))
    print('--------------------')

positive sentiment
chunk: [('thanks', 373), ('thank', 250), ('flight', 81), ('number', 76), ('help', 50), ('flight_number', 34), ('guys', 33), ('time', 33), ('way', 26), ('flights', 26)]
--------------------
negative sentiment
chunk: [('flight', 1078), ('number', 783), ('hold', 434), ('plane', 375), ('number_hours', 345), ('bag', 245), ('time', 242), ('flight_number', 240), ('hour', 239), ('thanks', 217)]
--------------------


# Term-Frequency Inverse Document Frequency

See if we can cluster tweets by their content using TF-IDF

In [960]:
# Find sentence boundaries and process them
df = pd.DataFrame()
df['text'] = data['text'].apply(sent_boundaries)
df['text_pro'] = df['text'].apply(rmstopwords).apply(tokenize_sent)
df['text_pro'] = df['text_pro'].apply(process_text).reset_index(drop=True)
df.head()

text  \
0   plus you've added commercials to the experien...   
1   it's really aggressive to blast obnoxious "en...   
2           and it's a really big bad thing about it   
3   seriously would pay $30 a flight for seats th...   
4   yes, nearly every time I fly VX this “ear wor...   

                                            text_pro  
0     plus youve added commercials experience tacky   
1  its really aggressive blast obnoxious entertai...  
2                           its really big bad thing  
3  seriously would pay number flight seats didnt ...  
4  yes nearly every time fly vx ear worm wont go ...

In [961]:
tfidf = TfidfVectorizer(min_df=10, max_features=10000, strip_accents='unicode',
                           analyzer='word', token_pattern=r'\w{1,}', ngram_range=(1,2),
                           use_idf=1, smooth_idf=1, sublinear_tf=1)

tfidf_text = tfidf.fit_transform(df['text_pro'])

In [989]:
tfidf_dict = dict(zip(tfidf.get_feature_names(), tfidf.idf_))
tfidf_dict = pd.DataFrame(tfidf.idf_, index=tfidf.get_feature_names(), columns=['tfidf_val'])
tfidf_dict.sort_values('tfidf_val', ascending=False, inplace=True)

In [992]:
from sklearn.decomposition import TruncatedSVD

svd = TruncatedSVD(n_components=50, random_state=0)
svd_tfidf = svd.fit_transform(tfidf_text)

In [994]:
from sklearn.manifold import TSNE

tsne_model = TSNE(n_components=2, verbose=1, random_state=0, learning_rate=1000)
tsne_tfidf = tsne_model.fit_transform(svd_tfidf)

[t-SNE] Computing pairwise distances...
[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Computed conditional probabilities for sample 1000 / 11381
[t-SNE] Computed conditional probabilities for sample 2000 / 11381
[t-SNE] Computed conditional probabilities for sample 3000 / 11381
[t-SNE] Computed conditional probabilities for sample 4000 / 11381
[t-SNE] Computed conditional probabilities for sample 5000 / 11381
[t-SNE] Computed conditional probabilities for sample 6000 / 11381
[t-SNE] Computed conditional probabilities for sample 7000 / 11381
[t-SNE] Computed conditional probabilities for sample 8000 / 11381
[t-SNE] Computed conditional probabilities for sample 9000 / 11381
[t-SNE] Computed conditional probabilities for sample 10000 / 11381
[t-SNE] Computed conditional probabilities for sample 11000 / 11381
[t-SNE] Computed conditional probabilities for sample 11381 / 11381
[t-SNE] Mean sigma: 0.000000
[t-SNE] KL divergence after 100 iterations with early exaggeration: 1.163407
[t-SN

In [999]:
tfidf_df = pd.DataFrame(tsne_tfidf, columns=['x', 'y'])
tfidf_df['description'] = df['text']

In [1000]:
tfidf_df.iplot(kind="scatter", x='x', y='y', mode='markers', size=5, text='description',
              dimensions=(750,500), margin=(50,50,50,50))

# Word2Vec

In [ ]:
import gensim
from gensim.models.word2vec import Word2Vec # the word2vec model gensim class
LabeledSentence = gensim.models.doc2vec.LabeledSentence # we'll talk about this down below

def labelizeTweets(tweets, label_type):
    labelized = []
    for i,v in enumerate(tweets):
        label = '%s_%s'%(label_type,i)
        labelized.append(LabeledSentence(v, [label]))
    return labelized

ngram_pos = pd.DataFrame(frequent_tokens('positive', 3, 1000), columns=['3-gram','counts'])
ngram_neg = pd.DataFrame(frequent_tokens('negative', 3, 1000), columns=['3-gram','counts'])

ngram = ngram_neg.append(ngram_pos).reset_index(drop=True)
#ngram = ngram['3-gram'].str.split('_')

ngram_lab = labelizeTweets(data['pro_text'].str.split(), 'TRAIN')

In [ ]:
ngram_w2v = Word2Vec(size=200, min_count=1)
ngram_w2v.build_vocab([x.words for x in ngram_lab])
ngram_w2v.train([x.words for x in ngram_lab])

In [ ]:
def w2v_trigram(text):
    m = 0
    text = text.split('_')
    for i in text:
        m += ngram_w2v[i]
    return m/len(text)

a = ngram['3-gram'].apply(w2v_trigram)
a = np.vstack(a)


def w2v_trigram(text):
    m = []
    text = text.split('_')
    for i in text:
        m = np.hstack([m,ngram_w2v[i]])
    return m/len(text)

a = ngram['3-gram'].apply(w2v_trigram)
a = np.vstack(a)

In [932]:
from sklearn.decomposition import TruncatedSVD

svd = TruncatedSVD(n_components=50, random_state=0)
svd_tfidf = svd.fit_transform(a)

In [933]:
from sklearn.manifold import TSNE

tsne_model = TSNE(n_components=2, verbose=1, random_state=0, learning_rate=10)
tsne_tfidf = tsne_model.fit_transform(svd_tfidf)

[t-SNE] Computing pairwise distances...
[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Computed conditional probabilities for sample 200 / 200
[t-SNE] Mean sigma: 0.951602
[t-SNE] KL divergence after 100 iterations with early exaggeration: 0.941546
[t-SNE] Error after 225 iterations: 0.941546


In [934]:
tfidf_df = pd.DataFrame(tsne_tfidf, columns=['x', 'y'])
tfidf_df['description'] = ngram['3-gram']

Try using plotly instead.

Use word2vec for each sentence or for each n-gram.

In [935]:
tfidf_df.iplot(kind="scatter", x='x', y='y', mode='markers', size=5, text='description',
              dimensions=(750,500), margin=(50,50,50,50))

In [ ]:
df['pro_text'] = df['text'].apply(process_text)
df['num_punc'] = df['text'].apply(num_exc_ques)
df['num_words'] = df['pro_text'].apply(num_words)

In [ ]:
import bokeh.plotting as bp
from bokeh.models import ColumnDataSource
from bokeh.models import HoverTool, BoxSelectTool
from bokeh.plotting import figure, show, output_notebook

output_notebook()

plot_tfidf = bp.figure(plot_width=700, plot_height=600, title="tf-idf clustering of sentences",
    tools="pan,wheel_zoom,box_zoom,reset,hover,previewsave",
    x_axis_type=None, y_axis_type=None, min_border=1)

In [ ]:
tfidf_df = pd.DataFrame(tsne_tfidf, columns=['x', 'y'])
tfidf_df['description'] = ngram['3-gram'].reset_index(drop=True)

In [ ]:
plot_tfidf.scatter(x='x', y='y', source=ColumnDataSource(tfidf_df))
hover = plot_tfidf.select(dict(type=HoverTool))
hover.tooltips={"description": "@description"}
show(plot_tfidf)